In [47]:
import pandas as pd
import numpy as np
from datetime import datetime
import scipy.stats as sp
import scipy.optimize as sco
import plotly
from plotly import graph_objs as go
from plotly.subplots import make_subplots
plotly.offline.init_notebook_mode(connected = True)

In [2]:
def BSM(S0, K, tau, r, sigma, opt_type='c', q=0):
    d1 = (np.log(S0/K)+(r-q+.5*sigma**2)*tau)/(sigma*np.sqrt(tau))
    d2 = d1 - sigma*np.sqrt(tau)
    N = lambda x: sp.norm.cdf(x)
    if opt_type == 'c':
        return S0*np.exp(-q*tau)*N(d1) - np.exp(-r*tau)*K*N(d2)
    else:
        return K*np.exp(-r*tau)*N(-d2) - S0*np.exp(-q*tau)*N(-d1)

In [18]:
files = ['20180427', '20180504', '20180511', '20180518', '20180525', '20180601', '20180608', '20180615',
        '20180720', '20180817', '20180921', '20181019', '20181116', '20190118', '20190215', '20190621',
        '20200117']
r = 0.0184 # 3m Treasury 4/30/18
dfs = []
for f in files:
    temp = pd.read_csv('{}.csv'.format(f))
    temp['TTM'] = (pd.to_datetime(temp['T'].apply(lambda x: str(x))) - pd.datetime(2018,4,27)).apply(lambda x: x.days)/365
    dfs.append(temp)
S = dfs[0].S[0]
dfs[0].TTM = 1/365
dfs

[     Unnamed: 0         T       K   P_bid   P_ask   C_bid   C_ask        S  \
 0             0  20180427   910.0    0.00    0.02  607.10  611.80  1517.96   
 1             1  20180427   920.0    0.00    0.03  596.50  601.50  1517.96   
 2             2  20180427   930.0    0.00    3.80  586.70  591.70  1517.96   
 3             3  20180427   940.0    0.00    0.05  576.50  581.50  1517.96   
 4             4  20180427   950.0    0.00    0.05  566.50  571.50  1517.96   
 5             5  20180427   960.0    0.00    1.67  556.40  561.40  1517.96   
 6             6  20180427   970.0    0.00    3.35  546.50  551.50  1517.96   
 7             7  20180427   980.0    0.00    4.25  536.50  541.50  1517.96   
 8             8  20180427   990.0    0.00    0.68  526.55  531.55  1517.96   
 9             9  20180427  1000.0    0.00    0.04  516.55  521.55  1517.96   
 10           10  20180427  1010.0    0.00    0.68  506.55  511.55  1517.96   
 11           11  20180427  1020.0    0.00    0.08  

In [19]:
tol = 10E-9
def SVI(df,a,b,p,m,sig):
    k = np.log(np.asarray(df.K)/(1517.96*np.exp(r*np.asarray(df.TTM))))
    return a + b*(p*(np.asarray(k)-m) + np.sqrt((np.asarray(k)-m)**2 + sig**2))
def SVI_fit(df,IV_col):
    obj = lambda x: np.sum((SVI(df, x[0], x[1], x[2], x[3], x[4]) - np.asarray(df[IV_col]))**2)
    cons = ({'type':'ineq','fun': lambda x: x[0] + x[1]*x[4]*np.sqrt(1 - x[2]**2)},
            {'type':'ineq','fun': lambda x: x[1]},
            {'type':'ineq','fun': lambda x: x[4] - tol})
    bnds = ((None,None),(0,None),(-1+tol,1-tol),(None,None),(tol,None))
    guess = [.01,.01,.01,.01,.01]
    result = sco.minimize(obj,guess,constraints=cons,bounds=bnds,tol=tol)
    return result

SVI_fit(dfs[0],'Comb_vol')

     fun: 1.6554086364248797
     jac: array([-0.00129673, -0.0003247 , -0.00082405,  0.00422643, -0.01618318])
 message: 'Optimization terminated successfully.'
    nfev: 392
     nit: 52
    njev: 52
  status: 0
 success: True
       x: array([-2.19707057, 11.7338407 ,  0.11266391,  0.04539798,  0.28811341])

In [22]:
fit511 = SVI_fit(dfs[2],'Comb_vol')['x']
df511 = pd.DataFrame({'K': np.linspace(900,2200,1301), 'TTM': dfs[2].TTM[0]})
df511['Sigma'] = SVI(df511,fit511[0],fit511[1],fit511[2],fit511[3],fit511[4])
df511['C'] = df511.apply(lambda x: BSM(S,x.K,x.TTM,r,x.Sigma), axis=1)
df511

K       TTM     Sigma           C
0      900.0  0.038356  1.249703  620.246532
1      901.0  0.038356  1.247203  619.246086
2      902.0  0.038356  1.244708  618.245659
3      903.0  0.038356  1.242218  617.245254
4      904.0  0.038356  1.239733  616.244869
5      905.0  0.038356  1.237253  615.244505
6      906.0  0.038356  1.234778  614.244162
7      907.0  0.038356  1.232308  613.243839
8      908.0  0.038356  1.229843  612.243538
9      909.0  0.038356  1.227383  611.243257
10     910.0  0.038356  1.224928  610.242998
11     911.0  0.038356  1.222477  609.242759
12     912.0  0.038356  1.220032  608.242542
13     913.0  0.038356  1.217591  607.242346
14     914.0  0.038356  1.215155  606.242171
15     915.0  0.038356  1.212725  605.242017
16     916.0  0.038356  1.210299  604.241885
17     917.0  0.038356  1.207878  603.241774
18     918.0  0.038356  1.205461  602.241685
19     919.0  0.038356  1.203050  601.241617
20     920.0  0.038356  1.200643  600.241571
21     921.0  0.038356  1.198242  599.241547
22     922.0  0.038356  1.195845  598.241544
23     923.0  0.038356  1.193453  597.241564
24     924.0  0.038356  1.191066  596.241605
25     925.0  0.038356  1.188683  595.241668
26     926.0  0.038356  1.186305  594.241753
27     927.0  0.038356  1.183932  593.241860
28     928.0  0.038356  1.181564  592.241990
29     929.0  0.038356  1.179201  591.242142
...      ...       ...       ...         ...
1271  2171.0  0.038356  0.684797    0.290718
1272  2172.0  0.038356  0.685877    0.291966
1273  2173.0  0.038356  0.686960    0.293226
1274  2174.0  0.038356  0.688044    0.294497
1275  2175.0  0.038356  0.689131    0.295780
1276  2176.0  0.038356  0.690219    0.297075
1277  2177.0  0.038356  0.691309    0.298381
1278  2178.0  0.038356  0.692401    0.299700
1279  2179.0  0.038356  0.693495    0.301030
1280  2180.0  0.038356  0.694591    0.302373
1281  2181.0  0.038356  0.695689    0.303727
1282  2182.0  0.038356  0.696789    0.305094
1283  2183.0  0.038356  0.697891    0.306473
1284  2184.0  0.038356  0.698995    0.307864
1285  2185.0  0.038356  0.700101    0.309267
1286  2186.0  0.038356  0.701208    0.310683
1287  2187.0  0.038356  0.702318    0.312111
1288  2188.0  0.038356  0.703429    0.313552
1289  2189.0  0.038356  0.704542    0.315005
1290  2190.0  0.038356  0.705658    0.316471
1291  2191.0  0.038356  0.706775    0.317950
1292  2192.0  0.038356  0.707894    0.319441
1293  2193.0  0.038356  0.709015    0.320945
1294  2194.0  0.038356  0.710138    0.322462
1295  2195.0  0.038356  0.711263    0.323992
1296  2196.0  0.038356  0.712390    0.325535
1297  2197.0  0.038356  0.713518    0.327092
1298  2198.0  0.038356  0.714649    0.328661
1299  2199.0  0.038356  0.715781    0.330243
1300  2200.0  0.038356  0.716916    0.331839

[1301 rows x 4 columns]

In [27]:
np.linspace(800,2200,2801)

array([ 800. ,  800.5,  801. , ..., 2199. , 2199.5, 2200. ])

In [28]:
fit427 = SVI_fit(dfs[0],'Comb_vol')['x']
df427 = pd.DataFrame({'K': np.linspace(800,2200,2801), 'TTM': dfs[0].TTM[0]})
df427['Sigma'] = SVI(df427,fit427[0],fit427[1],fit427[2],fit427[3],fit427[4])
df427['C'] = df427.apply(lambda x: BSM(S,x.K,x.TTM,r,x.Sigma), axis=1)
df427

K      TTM     Sigma           C
0      800.0  0.00274  5.626188  719.687114
1      800.5  0.00274  5.620255  719.185098
2      801.0  0.00274  5.614327  718.683083
3      801.5  0.00274  5.608404  718.181071
4      802.0  0.00274  5.602484  717.679061
5      802.5  0.00274  5.596570  717.177053
6      803.0  0.00274  5.590660  716.675047
7      803.5  0.00274  5.584755  716.173043
8      804.0  0.00274  5.578854  715.671041
9      804.5  0.00274  5.572959  715.169041
10     805.0  0.00274  5.567067  714.667043
11     805.5  0.00274  5.561180  714.165047
12     806.0  0.00274  5.555298  713.663054
13     806.5  0.00274  5.549420  713.161062
14     807.0  0.00274  5.543547  712.659072
15     807.5  0.00274  5.537679  712.157085
16     808.0  0.00274  5.531815  711.655099
17     808.5  0.00274  5.525956  711.153116
18     809.0  0.00274  5.520101  710.651135
19     809.5  0.00274  5.514251  710.149156
20     810.0  0.00274  5.508405  709.647178
21     810.5  0.00274  5.502564  709.145203
22     811.0  0.00274  5.496727  708.643230
23     811.5  0.00274  5.490895  708.141260
24     812.0  0.00274  5.485068  707.639291
25     812.5  0.00274  5.479245  707.137324
26     813.0  0.00274  5.473427  706.635359
27     813.5  0.00274  5.467613  706.133397
28     814.0  0.00274  5.461803  705.631437
29     814.5  0.00274  5.455998  705.129478
...      ...      ...       ...         ...
2771  2185.5  0.00274  3.268713    1.849258
2772  2186.0  0.00274  3.271008    1.851576
2773  2186.5  0.00274  3.273303    1.853898
2774  2187.0  0.00274  3.275598    1.856222
2775  2187.5  0.00274  3.277893    1.858549
2776  2188.0  0.00274  3.280188    1.860879
2777  2188.5  0.00274  3.282484    1.863211
2778  2189.0  0.00274  3.284779    1.865547
2779  2189.5  0.00274  3.287075    1.867885
2780  2190.0  0.00274  3.289370    1.870226
2781  2190.5  0.00274  3.291666    1.872569
2782  2191.0  0.00274  3.293962    1.874916
2783  2191.5  0.00274  3.296258    1.877265
2784  2192.0  0.00274  3.298554    1.879617
2785  2192.5  0.00274  3.300850    1.881972
2786  2193.0  0.00274  3.303147    1.884329
2787  2193.5  0.00274  3.305443    1.886689
2788  2194.0  0.00274  3.307740    1.889052
2789  2194.5  0.00274  3.310036    1.891418
2790  2195.0  0.00274  3.312333    1.893787
2791  2195.5  0.00274  3.314630    1.896158
2792  2196.0  0.00274  3.316927    1.898532
2793  2196.5  0.00274  3.319224    1.900909
2794  2197.0  0.00274  3.321521    1.903288
2795  2197.5  0.00274  3.323818    1.905671
2796  2198.0  0.00274  3.326115    1.908056
2797  2198.5  0.00274  3.328413    1.910443
2798  2199.0  0.00274  3.330710    1.912834
2799  2199.5  0.00274  3.333008    1.915227
2800  2200.0  0.00274  3.335306    1.917623

[2801 rows x 4 columns]

In [29]:
trace0 = go.Scatter(
    x = np.log(np.asarray(dfs[0].K)/(1517.96*np.exp(r*np.asarray(dfs[0].TTM)))), y = dfs[0].C_bid, name = 'Bid'
)
trace1 = go.Scatter(
    x = np.log(np.asarray(dfs[0].K)/(1517.96*np.exp(r*np.asarray(dfs[0].TTM)))), y = dfs[0].C_ask, name = 'Ask'
)
trace2 = go.Scatter(
    x = np.log(np.asarray(df427.K)/(1517.96*np.exp(r*np.asarray(df427.TTM)))), y = df427.C, name = 'SVI'
)

data  = [trace0,trace1,trace2]
layout = go.Layout(
    title = 'AMZN Call Raw SVI Date: 4-27-2018', 
        yaxis = dict(title = 'Call Price'), xaxis = dict(title = 'Normalized Strike'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [58]:
trace = go.Scatter(x = df427.K, y = (df427.C.shift(-1) - 2*df427.C + df427.C.shift(1))/.5**2, name = 'f(S)')
trace1 = go.Scatter(x = 100*[S], y = np.linspace(0,0.005,100), name = 'Underlying')
data = [trace, trace1]
layout = go.Layout(title = 'AMZN PDF: 4-27-2018', yaxis = dict(title = 'Probability Density'), xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [55]:
trace0 = go.Scatter(
    x = dfs[0].K, y = 100*dfs[0].Comb_vol, name = 'Implied Volatility'
)
trace1 = go.Scatter(
    x = df427.K, y = 100*df427.Sigma, name = 'SVI Fit'
)
trace2 = go.Scatter(
    x = df427.K, y = (df427.C.shift(-1) - 2*df427.C + df427.C.shift(1))/.5**2, name = 'PDF', yaxis = 'y2'
)

# data = [trace0,trace1]
# layout = go.Layout(
#     title = 'AMZN Implied Volatility: 4-27-2018', 
#     yaxis = dict(title = 'Implied Vol (%)'), 
#     yaxis2 = dict(title = 'Probability Density', side = 'right'), xaxis = dict(title = 'K'))
# fig = go.Figure(data=data, layout=layout)
fig = make_subplots(rows = 2, cols = 1)
fig.add_trace(trace0, row = 1, col = 1)
fig.add_trace(trace1, row = 1, col = 1)
fig.add_trace(trace2, row = 2, col = 1)
plotly.offline.iplot(fig)

In [63]:
for df in dfs:
    fit = SVI_fit(df,'Comb_vol')['x']
    temp = pd.DataFrame({'K': np.linspace(800,2200,2801), 'TTM': df.TTM[0]})
    temp['Sigma'] = SVI(temp,fit[0],fit[1],fit[2],fit[3],fit[4])
    temp['C'] = temp.apply(lambda x: BSM(S,x.K,x.TTM,r,x.Sigma), axis=1)
    trace0 = go.Scatter(
        x = df.K, y = 100*df.Comb_vol, name = 'Implied Volatility'
    )
    trace1 = go.Scatter(
        x = temp.K, y = 100*temp.Sigma, name = 'SVI Fit'
    )
    trace2 = go.Scatter(
        x = temp.K, y = (temp.C.shift(-1) - 2*temp.C + temp.C.shift(1))/.5**2, name = 'PDF', yaxis = 'y2'
    )
    fig = make_subplots(rows = 2, cols = 1)
    fig.add_trace(trace0, row = 1, col = 1)
    fig.add_trace(trace1, row = 1, col = 1)
    fig.add_trace(trace2, row = 2, col = 1)
    plotly.offline.iplot(fig)